In [1]:
import requests
from bs4 import BeautifulSoup

def pedido(limit=100, page=1,job_id=None):
    if job_id:
        url = f"https://api.itjobs.pt/job/get.json?api_key=ee176fa9456283ab9c42f357b036e236&id={job_id}"
    else:
        url = f"https://api.itjobs.pt/job/list.json?api_key=ee176fa9456283ab9c42f357b036e236&limit={limit}&page={page}"
    payload = {}
    headers = {'User-Agent': "ALPCD_5"}  # Necessário pôr 'User-Agent' nos headers
    res = requests.request("GET", url, headers=headers, data=payload)
    if res.status_code == 200:  # Verificar se o acesso foi bem sucedido (200 OK)
        results = res.json()
        return results
    else:
        print(f"Erro {res.status_code} - {res.text}")
        return {}

job_data = pedido()
limit = 100
page = 1
res = pedido(limit, page)
response = res
list_results= response["results"]
#soup = BeautifulSoup(res.text, "lxml")

while page*limit < response["total"]:
    page += 1
    new_results = pedido(limit, page)["results"]
    list_results += new_results
response["results"] = list_results


In [ ]:
import time
from datetime import datetime

sorted_results = sorted(list_results, key=lambda x: x['updatedAt'], reverse= True)
'''
up2 = 'sim'
for sort in sorted_results:
    up = sort["updatedAt"][:10]
    if up == up2:
        continue
    else:
        up2 = sort["updatedAt"][:10]
'''
given_skills = ['english']
start_date = '2024-11-03'       #PERGUNTAR AO PROFESSOR SE É NECESSARIO ACEITAR HORA TAMBEM
end_date = '2024-11-03'
start_date = datetime.strptime(start_date, '%Y-%m-%d')
end_date = datetime.strptime(end_date, '%Y-%m-%d')


filtered_results = []
for res in sorted_results:
    update_date_str = res['updatedAt'][:10]
    update_date = datetime.strptime(update_date_str, '%Y-%m-%d')
    if start_date <= update_date <= end_date:
        filtered_results.append(res)
print(f"A analisar {len(filtered_results)} resultados.")


A analisar 21 resultados.


In [4]:
for res in list_results:
    print(res)


{'id': 492110, 'company': {'id': 875, 'name': 'Mind Source', 'logo': 'https://static.itjobs.pt/images/companies/4b/0a5/875/logo.png', 'description': 'Somos uma Equipa especializada em Projectos de Consultoria e\xa0Outsourcing, Processos de Negócio e em Tecnologia. Investimos diariamente para sermos uma das melhores empresas para trabalhar, tendo sido distinguidos no ranking do Great Place to Work com o 3º lugar na categoria das empresas com 100 a 250 colaboradores. Destacamo-nos pelas práticas de gestão positiva do nosso Talento e pelo elevado grau de compromisso sentido pela nossa Equipa. É por tudo isto que as pessoas escolhem a Mind Source para trabalhar!\r\n\r\nTemos Projectos aliciantes à tua espera em Portugal, em várias capitais europeias e no Brasil onde já estamos a desenvolver soluções criativas com base nas tecnologias mais inovadoras do mercado.\r\n\r\nQueres saber mais sobre como ambicionamos mudar o mundo?\r\n\r\nSegue-nos em\xa0www.mindsource.pt', 'address': 'Rua Braamca

# Mine

In [15]:
# imports
import spacy
from spacy.matcher import PhraseMatcher
from skillNer.general_params import SKILL_DB
from skillNer.skill_extractor_class import SkillExtractor
from concurrent.futures import ThreadPoolExecutor, as_completed
from datetime import datetime

def filter_by_dates_results(list_results, start_date, end_date, given_skills):
    sorted_results = sorted(list_results, key=lambda x: x["updatedAt"], reverse=True)
    filtered_results = []
    count = 0

    for res in sorted_results:
        update_date_str = res['updatedAt'][:10]
        update_date = datetime.strptime(update_date_str, '%Y-%m-%d')
        if update_date <= end_date:
            if start_date <= update_date:
                count += 1
                print(count, end=', ')
                res = process_job(res, given_skills)
                filtered_results.append(res)
            else:
                break

    return filtered_results

def skills(given_skills, start_date, end_date, list_results):
    try:
        start_date = datetime.strptime(start_date, '%Y-%m-%d')
        end_date = datetime.strptime(end_date, '%Y-%m-%d')
    except ValueError:
        print("Erro ao ler as datas, verifique se estas existem.")
        return {}
    
    if end_date < start_date:
        print(f"Data final menor que inicial, a iniciar com valores trocados...")
        filtered_results = filter_by_dates_results(list_results, end_date, start_date, given_skills)
    else:
        filtered_results = filter_by_dates_results(list_results, start_date, end_date, given_skills)

    for result in filtered_results:
        if result:
            print(result)
        else:
            filtered_results.remove(result)

def process_job(res, given_skills):
    body = res['body']

    try:
        annotations = skill_extractor.annotate(body)
        
    except IndexError as e:
        print(f"Erro a 'anotar' o 'body': {body}")
        raise e
    except (IndexError, ValueError) as e:
        print(f"Erro a processar o 'body': {e}")
        return None

    annoted_skills = [skill['doc_node_value'] for skill in annotations['results']['full_matches']]
    annoted_skills += [skill['doc_node_value'] for skill in annotations['results']['ngram_scored']]

    if set(given_skills) & set(annoted_skills):      #PERGUNTAR AO PROFESSOR, se for todos as skills dadas all(item in annoted_skills for item in given_skills)
        return res
    else:
        return None

'''
def process_jobs_concurrently(list_of_results, given_skills, max_workers=4):
    results = []
    with ThreadPoolExecutor(max_workers=max_workers) as executor:
        future_to_res = {executor.submit(process_job, res, given_skills): res for res in list_of_results}

        for future in as_completed(future_to_res):
            res = future.result()
            if res:
                results.append(res)
                print(f"Processed job ID: {res['id']}")

    return results
'''
# iniciar o skill extractor
nlp = spacy.load("en_core_web_lg")
skill_extractor = SkillExtractor(nlp, SKILL_DB, PhraseMatcher)

# Given skills, start date, and end date
given_skills = ['english']
start_date = '2024-11-03'       #PERGUNTAR AO PROFESSOR SE É NECESSARIO ACEITAR HORA TAMBEM
end_date = '2024-11-03'

skills(given_skills, start_date, end_date, list_results)


loading full_matcher ...
loading abv_matcher ...
loading full_uni_matcher ...
loading low_form_matcher ...
loading token_matcher ...
1, 2, 3, 4, 5, 6, 7, 8, Erro a processar o 'body': 'special' is not in list
9, 10, 11, 12, 13, 14, 15, 16, Erro a processar o 'body': 'special' is not in list
17, 18, 19, 20, 21, {'id': 491865, 'company': {'id': 6731, 'name': 'YellowIpe', 'logo': 'https://static.itjobs.pt/images/companies/0e/915/6731/logo.png', 'description': 'YellowIpe® is your IT professional services consultancy. We offer the best tailored solutions for the requirements and challenges of your technological project.', 'url': 'https://yellowipe.io', 'url_facebook': 'https://www.facebook.com/yellowipe.io', 'url_linkedin': 'https://www.linkedin.com/company/yellowipe/', 'slug': 'yellowipe'}, 'companyId': 6731, 'title': 'Technical Writer', 'body': '<p><strong>About YellowIpe</strong><br /><br />Our mission is to inspire the connection between technology and people, we foster the best of our 

# S/ Skip 1

In [ ]:
import spacy
from spacy.matcher import PhraseMatcher
from skillNer.general_params import SKILL_DB
from skillNer.skill_extractor_class import SkillExtractor
from concurrent.futures import ThreadPoolExecutor, as_completed
from datetime import datetime

def filter_by_dates_results(list_results, start_date, end_date, given_skills):
    sorted_results = sorted(list_results, key=lambda x: x["updatedAt"], reverse=True)
    filtered_results = []

    for res in sorted_results:
        update_date_str = res['updatedAt'][:10]
        update_date = datetime.strptime(update_date_str, '%Y-%m-%d')
        if start_date <= update_date <= end_date:
            filtered_results.append(res)
        elif update_date < start_date:
            break

    return filtered_results

def skills(given_skills, start_date, end_date, list_results):
    try:
        start_date = datetime.strptime(start_date, '%Y-%m-%d')
        end_date = datetime.strptime(end_date, '%Y-%m-%d')
    except ValueError:
        print("Erro ao ler as datas, verifique se estas existem.")
        return {}
    
    if end_date < start_date:
        print("Data final menor que inicial, a iniciar com valores trocados...")
        filtered_results = filter_by_dates_results(list_results, end_date, start_date, given_skills)
    else:
        filtered_results = filter_by_dates_results(list_results, start_date, end_date, given_skills)

    results = process_jobs_concurrently(filtered_results, given_skills, max_workers=8)

    for result in results:
        if result:
            print(result)

def process_job(res, given_skills):
    body = res['body']
    try:
        annotations = skill_extractor.annotate(body)
    except (IndexError, ValueError) as e:
        print(f"Erro a processar o 'body': {e}")
        return None

    anoted_skills = set(skill['doc_node_value'] for skill in annotations['results']['full_matches'])
    anoted_skills.update(skill['doc_node_value'] for skill in annotations['results']['ngram_scored'])

    if set(given_skills) & anoted_skills:   #PERGUNTAR AO PROFESSOR, se for todos as skills dadas all(item in annoted_skills for item in given_skills)
        return res
    return None

def process_jobs_concurrently(list_of_results, given_skills, max_workers=4):
    results = []
    with ThreadPoolExecutor(max_workers=max_workers) as executor:
        future_to_res = {executor.submit(process_job, res, given_skills): res for res in list_of_results}

        for future in as_completed(future_to_res):
            res = future.result()
            if res:
                results.append(res)

    return results

# Iniciar o skill extractor
nlp = spacy.load("en_core_web_lg")
skill_extractor = SkillExtractor(nlp, SKILL_DB, PhraseMatcher)

# Given skills, start date, and end date
given_skills = ['english']
start_date = '2024-11-03'       #PERGUNTAR AO PROFESSOR SE É NECESSARIO ACEITAR HORA TAMBEM
end_date = '2024-11-03'

skills(given_skills, start_date, end_date, list_results)


loading full_matcher ...
loading abv_matcher ...
loading full_uni_matcher ...
loading low_form_matcher ...
loading token_matcher ...
Erro a processar o 'body': 'special' is not in list
Erro a processar o 'body': 'special' is not in list
{'id': 491865, 'company': {'id': 6731, 'name': 'YellowIpe', 'logo': 'https://static.itjobs.pt/images/companies/0e/915/6731/logo.png', 'description': 'YellowIpe® is your IT professional services consultancy. We offer the best tailored solutions for the requirements and challenges of your technological project.', 'url': 'https://yellowipe.io', 'url_facebook': 'https://www.facebook.com/yellowipe.io', 'url_linkedin': 'https://www.linkedin.com/company/yellowipe/', 'slug': 'yellowipe'}, 'companyId': 6731, 'title': 'Technical Writer', 'body': '<p><strong>About YellowIpe</strong><br /><br />Our mission is to inspire the connection between technology and people, we foster the best of our professionals through our expertise in finding and attracting the best tale

In [ ]:
import re
import time
import typer

app = typer.Typer()

@app.command()
def get_job_details_with_retry(job_id: str, retries=3, delay=2):
    url = f"https://api.itjobs.pt/job/{job_id}.json?api_key=ee176fa9456283ab9c42f357b036e236"
    headers = {'User-Agent': "ALPCD_5"}
    for attempt in range(retries):
        try:
            res = requests.get(url, headers=headers)
            res.raise_for_status()  # Levanta um erro HTTP se houver um problema
            return res.json()
        except requests.exceptions.HTTPError as http_err:
            if res.status_code == 500 and attempt < retries - 1:
                print(f"Erro 500 - Tentando novamente em {delay} segundos...")
                time.sleep(delay)
            else:
                print(f"Erro HTTP: {http_err}")
                return None
        except requests.exceptions.RequestException as req_err:
            print(f"Erro na requisição: {req_err}")
            return None
    return None

# Comando para extrair o salário de um job específico
@app.command()
def salary(job_id: str):
    # Usar a função com retentativa para obter os detalhes do job
    job_data = get_job_details_with_retry(job_id)
    
    if job_data is None:
        print("Não foi possível obter os dados do job. Verifique o job_id e tente novamente.")
        return
    
    # Verificar se o campo wage está presente e tem valor
    wage = job_data.get("wage")
    if wage:
        print(f"Salário encontrado: {wage}")
    else:
        # Caso wage esteja vazio ou seja None, procurar por valores salariais em outros campos
        description = job_data.get("description", "")
        matches = re.findall(r"\b\d{1,3}(?:\.\d{3})*(?:,\d{2})?\b", description)
        
        if matches:
            # Exibe o primeiro valor encontrado que pode representar um salário
            salary_estimate = matches[0]
            print(f"Salário estimado encontrado na descrição: {salary_estimate}")
        else:
            print("Salário não especificado na oferta de emprego.")

if __name__ == "_main_":
    app()  # Executa a aplicação Typer